In [4]:
pip install opencv-python

In [5]:
import os
import torch
import torch.nn as nn
from torchvision import models, transforms
from PIL import Image
import numpy as np
import matplotlib.pyplot as plt
import cv2
import numpy as np
from matplotlib import pyplot as plt

In [13]:
import os
import torch
from torchvision.models import densenet121
from torchvision.io import read_image
from torchvision import transforms
from PIL import Image

# Step 1: Initialize model with pre-trained weights
model = densenet121(pretrained=True)
model.eval()

# Step 2: Initialize the inference transforms
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# Specify the path to the folder containing the images
folder_path = "C:/Users/DandaC8719/Documents/capstone_overall_code/original_incorrect_predictions_folder(RFGSM)_DenseNet"
# Step 3: Iterate through images in the folder
FGSM_Images_ModelRun_class_ids = []
for filename in os.listdir(folder_path):
    if filename.endswith('.jpg') or filename.endswith('.JPEG'):
        # Construct the full path to the image
        image_path = os.path.join(folder_path, filename)

        # Use torchvision to read the image
        img = read_image(image_path)
        
        # Convert tensor image to PIL Image
        img_pil = transforms.ToPILImage()(img)

        # Step 4: Apply inference preprocessing transforms
        batch = preprocess(img_pil).unsqueeze(0)

        # Step 5: Use the model and collect the predicted class IDs
        with torch.no_grad():
            prediction = model(batch).squeeze(0).softmax(0)
            class_id = prediction.argmax().item()
            FGSM_Images_ModelRun_class_ids.append(class_id)
            score = prediction[class_id].item()
            #category_name = weights.meta["categories"][class_id]
            print(f"{filename}: {100 * score:.1f}%")
#print("Class ID's of FGSM images after running them through the model",FGSM_Images_ModelRun_class_ids)
print(len(FGSM_Images_ModelRun_class_ids)) 

ILSVRC2012_val_00000001.JPEG: 65.2%
ILSVRC2012_val_00000004.JPEG: 44.2%
ILSVRC2012_val_00000005.JPEG: 53.4%
ILSVRC2012_val_00000006.JPEG: 35.0%
ILSVRC2012_val_00000007.JPEG: 99.2%
ILSVRC2012_val_00000013.JPEG: 94.5%
ILSVRC2012_val_00000021.JPEG: 75.2%
ILSVRC2012_val_00000029.JPEG: 29.7%
ILSVRC2012_val_00000032.JPEG: 67.6%
ILSVRC2012_val_00000034.JPEG: 78.3%
ILSVRC2012_val_00000039.JPEG: 32.3%
ILSVRC2012_val_00000040.JPEG: 54.5%
ILSVRC2012_val_00000042.JPEG: 94.5%
ILSVRC2012_val_00000044.JPEG: 90.1%
ILSVRC2012_val_00000045.JPEG: 98.2%
ILSVRC2012_val_00000046.JPEG: 22.6%
ILSVRC2012_val_00000049.JPEG: 70.7%
ILSVRC2012_val_00000051.JPEG: 98.9%
ILSVRC2012_val_00000054.JPEG: 98.5%
ILSVRC2012_val_00000061.JPEG: 44.3%
ILSVRC2012_val_00000063.JPEG: 77.2%
ILSVRC2012_val_00000064.JPEG: 51.4%
ILSVRC2012_val_00000065.JPEG: 69.4%
ILSVRC2012_val_00000068.JPEG: 85.8%
ILSVRC2012_val_00000069.JPEG: 99.5%
ILSVRC2012_val_00000072.JPEG: 99.9%
ILSVRC2012_val_00000077.JPEG: 84.2%
ILSVRC2012_val_00000079.JPEG

In [14]:
input_directory = "./adversarial_images_folder(RFGSM)_DenseNet"
output_directory = "./Blurred_images(MedianBlur)RFGSM_DenseNet"
#Median Blur
os.makedirs(output_directory, exist_ok=True)

# Iterate over input images
input_images = [os.path.join(input_directory, filename) for filename in os.listdir(input_directory) if filename.endswith(".JPEG")]

for input_image_path in input_images:
    # Load the image using cv2.imread()
    image_BGR = cv2.imread(input_image_path)
    
    # Apply median blur
    median_blur = cv2.medianBlur(image_BGR, 5)  # Adjust the kernel size (5 in this case)
    
    # Save the blurred image
    output_image_path = os.path.join(output_directory, os.path.basename(input_image_path))
    cv2.imwrite(output_image_path, median_blur)

In [15]:
input_directory = "./adversarial_images_folder(RFGSM)_DenseNet"
output_directory = "./Blurred_images(Gaussian)RFGSM_DenseNet"

# GaussianBlur
os.makedirs(output_directory, exist_ok=True)
input_images = [os.path.join(input_directory, filename) for filename in os.listdir(input_directory) if filename.endswith(".JPEG")]   
    
# Define parameters for Gaussian blur
kernel_size = (5, 5)  # Adjust the kernel size as needed

# Define parameters for contrast enhancement
alpha = 1.5  # Adjust the contrast factor as needed
beta = 0  # Adjust the brightness factor as needed

# Apply preprocessing to each input image
for input_image_path in input_images:
    # Load the image using cv2.imread()
    image_BGR = cv2.imread(input_image_path)
    # Apply Gaussian blur
    blurred_image = cv2.GaussianBlur(image_BGR, kernel_size, 0)
    # Apply contrast enhancement
    enhanced_image = cv2.convertScaleAbs(blurred_image, alpha=alpha, beta=beta)
    # Save the preprocessed image
    output_image_path = os.path.join(output_directory, os.path.basename(input_image_path))
    cv2.imwrite(output_image_path, enhanced_image)


In [16]:
input_directory = "./adversarial_images_folder(RFGSM)_DenseNet"
output_directory = "./Blurred_images(Bilateral)RFGSM_DenseNet"
#BilateralBlur
os.makedirs(output_directory, exist_ok=True)
input_images = [os.path.join(input_directory, filename) for filename in os.listdir(input_directory) if filename.endswith(".JPEG")]
for input_image_path in input_images:
    # Load the image using cv2.imread()
    image_BGR = cv2.imread(input_image_path)
    # Convert BGR to RGB
    image_RGB = cv2.cvtColor(image_BGR, cv2.COLOR_BGR2RGB)
    # Apply bilateral blur
    bilateral_blur = cv2.bilateralFilter(image_RGB, 23, 51, 51)
    # Save the blurred image
    output_image_path = os.path.join(output_directory, os.path.basename(input_image_path))
    cv2.imwrite(output_image_path, bilateral_blur)

In [17]:
input_directory = "./adversarial_images_folder(RFGSM)_DenseNet"
output_directory = "./Blurred_images(Affine)RFGSM_DenseNet"
#Affine Transformation
# Create the output directory if it doesn't exist
os.makedirs(output_directory, exist_ok=True)
# Load input images
input_images = [os.path.join(input_directory, filename) for filename in os.listdir(input_directory) if filename.endswith(".JPEG")]

# Define the affine transformation matrix
matrix = np.float32([[1, 0, 50],   # Translation in x-direction
                     [0, 1, -30]])  # Translation in y-direction
# Apply affine transformation to each input image
for input_image_path in input_images:
    # Load the image using cv2.imread()
    image_BGR = cv2.imread(input_image_path)
    # Apply affine transformation
    transformed_image = cv2.warpAffine(image_BGR, matrix, (image_BGR.shape[1], image_BGR.shape[0]))
    # Save the preprocessed image
    output_image_path = os.path.join(output_directory, os.path.basename(input_image_path))
    cv2.imwrite(output_image_path, transformed_image)

In [18]:
import os
import torch
from torchvision.models import densenet121
from torchvision.io import read_image
from torchvision import transforms
from PIL import Image

# Step 1: Initialize model with pre-trained weights
model = densenet121(pretrained=True)
model.eval()

# Step 2: Initialize the inference transforms
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])


# Step 2: Initialize the inference transforms
Median_BlurredImages_ModelRun_class_ids = []
 
# Specify the path to the folder containing the images
folder_path = "C:/Users/DandaC8719/Documents/capstone_overall_code/Blurred_images(MedianBlur)RFGSM_DenseNet"

for filename in os.listdir(folder_path):
    if filename.endswith('.jpg') or filename.endswith('.JPEG'):
        # Construct the full path to the image
        image_path = os.path.join(folder_path, filename)

        # Use torchvision to read the image
        img = read_image(image_path)
        
        # Convert tensor image to PIL Image
        img_pil = transforms.ToPILImage()(img)

        # Step 4: Apply inference preprocessing transforms
        batch = preprocess(img_pil).unsqueeze(0)

        # Step 5: Use the model and collect the predicted class IDs
        with torch.no_grad():
            prediction = model(batch).squeeze(0).softmax(0)
            class_id = prediction.argmax().item()
            Median_BlurredImages_ModelRun_class_ids.append(class_id)
            score = prediction[class_id].item()
            print(f"{filename}: {100 * score:.1f}%")
#print("Class ID's of Bilateral blurred images after running them through the model",Bilateral_BlurredImages_ModelRun_class_ids)
print(len(Median_BlurredImages_ModelRun_class_ids))

perturbed_ILSVRC2012_val_00000001.JPEG: 52.1%
perturbed_ILSVRC2012_val_00000004.JPEG: 50.7%
perturbed_ILSVRC2012_val_00000005.JPEG: 34.1%
perturbed_ILSVRC2012_val_00000006.JPEG: 30.8%
perturbed_ILSVRC2012_val_00000007.JPEG: 9.9%
perturbed_ILSVRC2012_val_00000013.JPEG: 79.0%
perturbed_ILSVRC2012_val_00000021.JPEG: 30.0%
perturbed_ILSVRC2012_val_00000029.JPEG: 52.6%
perturbed_ILSVRC2012_val_00000032.JPEG: 42.6%
perturbed_ILSVRC2012_val_00000034.JPEG: 27.2%
perturbed_ILSVRC2012_val_00000039.JPEG: 20.3%
perturbed_ILSVRC2012_val_00000040.JPEG: 28.2%
perturbed_ILSVRC2012_val_00000042.JPEG: 52.8%
perturbed_ILSVRC2012_val_00000044.JPEG: 56.9%
perturbed_ILSVRC2012_val_00000045.JPEG: 81.3%
perturbed_ILSVRC2012_val_00000046.JPEG: 14.9%
perturbed_ILSVRC2012_val_00000049.JPEG: 31.1%
perturbed_ILSVRC2012_val_00000051.JPEG: 74.0%
perturbed_ILSVRC2012_val_00000054.JPEG: 37.8%
perturbed_ILSVRC2012_val_00000061.JPEG: 17.5%
perturbed_ILSVRC2012_val_00000063.JPEG: 71.3%
perturbed_ILSVRC2012_val_00000064.J

In [19]:
import os
import torch
from torchvision.models import densenet121
from torchvision.io import read_image
from torchvision import transforms
from PIL import Image

# Step 1: Initialize model with pre-trained weights
model = densenet121(pretrained=True)
model.eval()

# Step 2: Initialize the inference transforms
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])


# Step 2: Initialize the inference transforms
Gaussian_BlurredImages_ModelRun_class_ids = []
 
# Specify the path to the folder containing the images
folder_path = "C:/Users/DandaC8719/Documents/capstone_overall_code/Blurred_images(Gaussian)RFGSM_DenseNet"

for filename in os.listdir(folder_path):
    if filename.endswith('.jpg') or filename.endswith('.JPEG'):
        # Construct the full path to the image
        image_path = os.path.join(folder_path, filename)

        # Use torchvision to read the image
        img = read_image(image_path)
        
        # Convert tensor image to PIL Image
        img_pil = transforms.ToPILImage()(img)

        # Step 4: Apply inference preprocessing transforms
        batch = preprocess(img_pil).unsqueeze(0)

        # Step 5: Use the model and collect the predicted class IDs
        with torch.no_grad():
            prediction = model(batch).squeeze(0).softmax(0)
            class_id = prediction.argmax().item()
            Gaussian_BlurredImages_ModelRun_class_ids.append(class_id)
            score = prediction[class_id].item()
            print(f"{filename}: {100 * score:.1f}%")
#print("Class ID's of Bilateral blurred images after running them through the model",Bilateral_BlurredImages_ModelRun_class_ids)
print(len(Gaussian_BlurredImages_ModelRun_class_ids))

perturbed_ILSVRC2012_val_00000001.JPEG: 12.1%
perturbed_ILSVRC2012_val_00000004.JPEG: 59.2%
perturbed_ILSVRC2012_val_00000005.JPEG: 20.1%
perturbed_ILSVRC2012_val_00000006.JPEG: 21.1%
perturbed_ILSVRC2012_val_00000007.JPEG: 13.8%
perturbed_ILSVRC2012_val_00000013.JPEG: 92.9%
perturbed_ILSVRC2012_val_00000021.JPEG: 44.4%
perturbed_ILSVRC2012_val_00000029.JPEG: 55.2%
perturbed_ILSVRC2012_val_00000032.JPEG: 60.4%
perturbed_ILSVRC2012_val_00000034.JPEG: 23.0%
perturbed_ILSVRC2012_val_00000039.JPEG: 13.7%
perturbed_ILSVRC2012_val_00000040.JPEG: 66.4%
perturbed_ILSVRC2012_val_00000042.JPEG: 10.9%
perturbed_ILSVRC2012_val_00000044.JPEG: 38.6%
perturbed_ILSVRC2012_val_00000045.JPEG: 58.8%
perturbed_ILSVRC2012_val_00000046.JPEG: 39.9%
perturbed_ILSVRC2012_val_00000049.JPEG: 33.7%
perturbed_ILSVRC2012_val_00000051.JPEG: 74.4%
perturbed_ILSVRC2012_val_00000054.JPEG: 5.8%
perturbed_ILSVRC2012_val_00000061.JPEG: 5.3%
perturbed_ILSVRC2012_val_00000063.JPEG: 84.4%
perturbed_ILSVRC2012_val_00000064.JP

In [20]:
import os
import torch
from torchvision.models import densenet121
from torchvision.io import read_image
from torchvision import transforms
from PIL import Image

# Step 1: Initialize model with pre-trained weights
model = densenet121(pretrained=True)
model.eval()

# Step 2: Initialize the inference transforms
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])


# Step 2: Initialize the inference transforms
Bilateral_BlurredImages_ModelRun_class_ids = []
 
# Specify the path to the folder containing the images
folder_path = "C:/Users/DandaC8719/Documents/capstone_overall_code/Blurred_images(Bilateral)RFGSM_DenseNet"

for filename in os.listdir(folder_path):
    if filename.endswith('.jpg') or filename.endswith('.JPEG'):
        # Construct the full path to the image
        image_path = os.path.join(folder_path, filename)

        # Use torchvision to read the image
        img = read_image(image_path)
        
        # Convert tensor image to PIL Image
        img_pil = transforms.ToPILImage()(img)

        # Step 4: Apply inference preprocessing transforms
        batch = preprocess(img_pil).unsqueeze(0)

        # Step 5: Use the model and collect the predicted class IDs
        with torch.no_grad():
            prediction = model(batch).squeeze(0).softmax(0)
            class_id = prediction.argmax().item()
            Bilateral_BlurredImages_ModelRun_class_ids.append(class_id)
            score = prediction[class_id].item()
            print(f"{filename}: {100 * score:.1f}%")
#print("Class ID's of Bilateral blurred images after running them through the model",Bilateral_BlurredImages_ModelRun_class_ids)
print(len(Bilateral_BlurredImages_ModelRun_class_ids))

perturbed_ILSVRC2012_val_00000001.JPEG: 40.2%
perturbed_ILSVRC2012_val_00000004.JPEG: 76.5%
perturbed_ILSVRC2012_val_00000005.JPEG: 64.2%
perturbed_ILSVRC2012_val_00000006.JPEG: 38.8%
perturbed_ILSVRC2012_val_00000007.JPEG: 89.0%
perturbed_ILSVRC2012_val_00000013.JPEG: 45.5%
perturbed_ILSVRC2012_val_00000021.JPEG: 39.9%
perturbed_ILSVRC2012_val_00000029.JPEG: 61.4%
perturbed_ILSVRC2012_val_00000032.JPEG: 34.8%
perturbed_ILSVRC2012_val_00000034.JPEG: 13.8%
perturbed_ILSVRC2012_val_00000039.JPEG: 21.4%
perturbed_ILSVRC2012_val_00000040.JPEG: 44.3%
perturbed_ILSVRC2012_val_00000042.JPEG: 47.0%
perturbed_ILSVRC2012_val_00000044.JPEG: 33.4%
perturbed_ILSVRC2012_val_00000045.JPEG: 77.7%
perturbed_ILSVRC2012_val_00000046.JPEG: 63.2%
perturbed_ILSVRC2012_val_00000049.JPEG: 85.4%
perturbed_ILSVRC2012_val_00000051.JPEG: 36.0%
perturbed_ILSVRC2012_val_00000054.JPEG: 63.6%
perturbed_ILSVRC2012_val_00000061.JPEG: 8.9%
perturbed_ILSVRC2012_val_00000063.JPEG: 5.9%
perturbed_ILSVRC2012_val_00000064.JP

In [21]:
import os
import torch
from torchvision.models import densenet121
from torchvision.io import read_image
from torchvision import transforms
from PIL import Image

# Step 1: Initialize model with pre-trained weights
model = densenet121(pretrained=True)
model.eval()

# Step 2: Initialize the inference transforms
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])


# Step 2: Initialize the inference transforms
Affine_BlurredImages_ModelRun_class_ids = []
 
# Specify the path to the folder containing the images
folder_path = "C:/Users/DandaC8719/Documents/capstone_overall_code/Blurred_images(Affine)RFGSM_DenseNet"

for filename in os.listdir(folder_path):
    if filename.endswith('.jpg') or filename.endswith('.JPEG'):
        # Construct the full path to the image
        image_path = os.path.join(folder_path, filename)

        # Use torchvision to read the image
        img = read_image(image_path)
        
        # Convert tensor image to PIL Image
        img_pil = transforms.ToPILImage()(img)

        # Step 4: Apply inference preprocessing transforms
        batch = preprocess(img_pil).unsqueeze(0)

        # Step 5: Use the model and collect the predicted class IDs
        with torch.no_grad():
            prediction = model(batch).squeeze(0).softmax(0)
            class_id = prediction.argmax().item()
            Affine_BlurredImages_ModelRun_class_ids.append(class_id)
            score = prediction[class_id].item()
            print(f"{filename}: {100 * score:.1f}%")
#print("Class ID's of Bilateral blurred images after running them through the model",Bilateral_BlurredImages_ModelRun_class_ids)
print(len(Affine_BlurredImages_ModelRun_class_ids))

perturbed_ILSVRC2012_val_00000001.JPEG: 28.7%
perturbed_ILSVRC2012_val_00000004.JPEG: 46.1%
perturbed_ILSVRC2012_val_00000005.JPEG: 45.4%
perturbed_ILSVRC2012_val_00000006.JPEG: 20.8%
perturbed_ILSVRC2012_val_00000007.JPEG: 23.7%
perturbed_ILSVRC2012_val_00000013.JPEG: 75.2%
perturbed_ILSVRC2012_val_00000021.JPEG: 60.4%
perturbed_ILSVRC2012_val_00000029.JPEG: 64.1%
perturbed_ILSVRC2012_val_00000032.JPEG: 25.9%
perturbed_ILSVRC2012_val_00000034.JPEG: 31.6%
perturbed_ILSVRC2012_val_00000039.JPEG: 32.6%
perturbed_ILSVRC2012_val_00000040.JPEG: 18.9%
perturbed_ILSVRC2012_val_00000042.JPEG: 10.9%
perturbed_ILSVRC2012_val_00000044.JPEG: 43.7%
perturbed_ILSVRC2012_val_00000045.JPEG: 26.5%
perturbed_ILSVRC2012_val_00000046.JPEG: 43.8%
perturbed_ILSVRC2012_val_00000049.JPEG: 27.8%
perturbed_ILSVRC2012_val_00000051.JPEG: 98.6%
perturbed_ILSVRC2012_val_00000054.JPEG: 59.7%
perturbed_ILSVRC2012_val_00000061.JPEG: 7.3%
perturbed_ILSVRC2012_val_00000063.JPEG: 46.9%
perturbed_ILSVRC2012_val_00000064.J

In [22]:
# Assuming you have already executed the code snippets to obtain the arrays

# Create sets from the arrays for efficient comparison
median_set = (Median_BlurredImages_ModelRun_class_ids)
FGSM_set = (FGSM_Images_ModelRun_class_ids)

# Ensure both lists have the same length
if len(Median_BlurredImages_ModelRun_class_ids) != len(FGSM_Images_ModelRun_class_ids):
    print("Lists have different lengths. Cannot compare.")
else:
    # Initialize a counter for matching elements
    matching_count = 0

    # Iterate over the indices of the lists
    for i in range(len(Median_BlurredImages_ModelRun_class_ids)):
        # Compare elements at the same index in both lists
        if Median_BlurredImages_ModelRun_class_ids[i] == FGSM_Images_ModelRun_class_ids[i]:
            # If they match, increment the matching count
            matching_count += 1

    print("Number of matching elements:", matching_count)

Number of matching elements: 9898


In [23]:
# Assuming you have already executed the code snippets to obtain the arrays

# Create sets from the arrays for efficient comparison
gaussian_set = (Gaussian_BlurredImages_ModelRun_class_ids)
FGSM_set = (FGSM_Images_ModelRun_class_ids)

# Ensure both lists have the same length
if len(Gaussian_BlurredImages_ModelRun_class_ids) != len(FGSM_Images_ModelRun_class_ids):
    print("Lists have different lengths. Cannot compare.")
else:
    # Initialize a counter for matching elements
    matching_count = 0

    # Iterate over the indices of the lists
    for i in range(len(Gaussian_BlurredImages_ModelRun_class_ids)):
        # Compare elements at the same index in both lists
        if Gaussian_BlurredImages_ModelRun_class_ids[i] == FGSM_Images_ModelRun_class_ids[i]:
            # If they match, increment the matching count
            matching_count += 1

    print("Number of matching elements:", matching_count)

Number of matching elements: 9685


In [24]:
# Assuming you have already executed the code snippets to obtain the arrays

# Create sets from the arrays for efficient comparison
bilateral_set = (Bilateral_BlurredImages_ModelRun_class_ids)
FGSM_set = (FGSM_Images_ModelRun_class_ids)

# Ensure both lists have the same length
if len(Bilateral_BlurredImages_ModelRun_class_ids) != len(FGSM_Images_ModelRun_class_ids):
    print("Lists have different lengths. Cannot compare.")
else:
    # Initialize a counter for matching elements
    matching_count = 0

    # Iterate over the indices of the lists
    for i in range(len(Bilateral_BlurredImages_ModelRun_class_ids)):
        # Compare elements at the same index in both lists
        if Bilateral_BlurredImages_ModelRun_class_ids[i] == FGSM_Images_ModelRun_class_ids[i]:
            # If they match, increment the matching count
            matching_count += 1

    print("Number of matching elements:", matching_count)

Number of matching elements: 7300


In [25]:
# Assuming you have already executed the code snippets to obtain the arrays

# Create sets from the arrays for efficient comparison
affine_set = (Affine_BlurredImages_ModelRun_class_ids)
FGSM_set = (FGSM_Images_ModelRun_class_ids)

# Ensure both lists have the same length
if len(Affine_BlurredImages_ModelRun_class_ids) != len(FGSM_Images_ModelRun_class_ids):
    print("Lists have different lengths. Cannot compare.")
else:
    # Initialize a counter for matching elements
    matching_count = 0

    # Iterate over the indices of the lists
    for i in range(len(Affine_BlurredImages_ModelRun_class_ids)):
        # Compare elements at the same index in both lists
        if Affine_BlurredImages_ModelRun_class_ids[i] == FGSM_Images_ModelRun_class_ids[i]:
            # If they match, increment the matching count
            matching_count += 1

    print("Number of matching elements:", matching_count)

Number of matching elements: 9867
